In [ ]:
!nvidia-smi

Wed Feb 22 00:06:08 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 510.47.03    Driver Version: 510.47.03    CUDA Version: 11.6     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   55C    P0    27W /  70W |      0MiB / 15360MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
!pip install dataframe-image


In [ ]:
import pandas as pd 
import numpy as np
import plotly.express as px
import tensorflow as tf
from keras.models import Sequential
from keras.layers import Dense, LSTM, Dropout,GRU
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split

In [ ]:
dataframe = pd.read_csv("/content/drive/MyDrive/new_article/FoodDeleveryTimePrediction/deliverytimehistory.txt")
dataframe.head()

ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0  4607     INDORES13DEL02                   37                      4.9   
1  B379     BANGRES18DEL02                   34                      4.5   
2  5D6D     BANGRES19DEL01                   23                      4.4   
3  7A6A    COIMBRES13DEL02                   38                      4.7   
4  70A2     CHENRES12DEL01                   32                      4.6   

   Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0            22.745049             75.892471                   22.765049   
1            12.913041             77.683237                   13.043041   
2            12.914264             77.678400                   12.924264   
3            11.003669             76.976494                   11.053669   
4            12.972793             80.249982                   13.012793   

   Delivery_location_longitude Type_of_order Type_of_vehicle  Time_taken(min)  
0                    75.912471        Snack      motorcycle                24  
1                    77.813237        Snack         scooter                33  
2                    77.688400       Drinks      motorcycle                26  
3                    77.026494       Buffet      motorcycle                21  
4                    80.289982        Snack         scooter                30

In [ ]:
import dataframe_image as dfi
dfi.export(dataframe.head(),"first_image.png",max_rows=5,table_conversion='crome',fontsize=10)

In [ ]:
dataframe.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45593 entries, 0 to 45592
Data columns (total 11 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   ID                           45593 non-null  object 
 1   Delivery_person_ID           45593 non-null  object 
 2   Delivery_person_Age          45593 non-null  int64  
 3   Delivery_person_Ratings      45593 non-null  float64
 4   Restaurant_latitude          45593 non-null  float64
 5   Restaurant_longitude         45593 non-null  float64
 6   Delivery_location_latitude   45593 non-null  float64
 7   Delivery_location_longitude  45593 non-null  float64
 8   Type_of_order                45593 non-null  object 
 9   Type_of_vehicle              45593 non-null  object 
 10  Time_taken(min)              45593 non-null  int64  
dtypes: float64(5), int64(2), object(4)
memory usage: 3.8+ MB


In [ ]:
dataframe.isnull().sum()

ID                             0
Delivery_person_ID             0
Delivery_person_Age            0
Delivery_person_Ratings        0
Restaurant_latitude            0
Restaurant_longitude           0
Delivery_location_latitude     0
Delivery_location_longitude    0
Type_of_order                  0
Type_of_vehicle                0
Time_taken(min)                0
dtype: int64

In [ ]:
# Set the earth's radius value (in kilometers)
R = 6371

# Convert degrees to radians
def degree_to_radians(degrees):
    return degrees * (np.pi/180)

# Using herversine formula to calculate the distance between to points
def distcalculate(lat1, lon1, lat2, lon2):
    d_lat = degree_to_radians(lat2-lat1)
    d_lon = degree_to_radians(lon2-lon1)
    a = np.sin(d_lat/2)**2 + np.cos(degree_to_radians(lat1)) * np.cos(degree_to_radians(lat2)) * np.sin(d_lon/2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1-a))
    return R * c
  
# Calculate the distance between each pair of points
dataframe['distance'] = np.nan

for i in range(len(dataframe)):
    dataframe.loc[i, 'distance'] = distcalculate(dataframe.loc[i, 'Restaurant_latitude'], 
                                        dataframe.loc[i, 'Restaurant_longitude'], 
                                        dataframe.loc[i, 'Delivery_location_latitude'], 
                                        dataframe.loc[i, 'Delivery_location_longitude'])

In [ ]:
dataframe

ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0      4607     INDORES13DEL02                   37                      4.9   
1      B379     BANGRES18DEL02                   34                      4.5   
2      5D6D     BANGRES19DEL01                   23                      4.4   
3      7A6A    COIMBRES13DEL02                   38                      4.7   
4      70A2     CHENRES12DEL01                   32                      4.6   
...     ...                ...                  ...                      ...   
45588  7C09      JAPRES04DEL01                   30                      4.8   
45589  D641      AGRRES16DEL01                   21                      4.6   
45590  4F8D     CHENRES08DEL03                   30                      4.9   
45591  5EEE    COIMBRES11DEL01                   20                      4.7   
45592  5FB2   RANCHIRES09DEL02                   23                      4.9   

       Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0                22.745049             75.892471                   22.765049   
1                12.913041             77.683237                   13.043041   
2                12.914264             77.678400                   12.924264   
3                11.003669             76.976494                   11.053669   
4                12.972793             80.249982                   13.012793   
...                    ...                   ...                         ...   
45588            26.902328             75.794257                   26.912328   
45589             0.000000              0.000000                    0.070000   
45590            13.022394             80.242439                   13.052394   
45591            11.001753             76.986241                   11.041753   
45592            23.351058             85.325731                   23.431058   

       Delivery_location_longitude Type_of_order Type_of_vehicle  \
0                        75.912471        Snack      motorcycle    
1                        77.813237        Snack         scooter    
2                        77.688400       Drinks      motorcycle    
3                        77.026494       Buffet      motorcycle    
4                        80.289982        Snack         scooter    
...                            ...           ...             ...   
45588                    75.804257         Meal      motorcycle    
45589                     0.070000       Buffet      motorcycle    
45590                    80.272439       Drinks         scooter    
45591                    77.026241        Snack      motorcycle    
45592                    85.405731        Snack         scooter    

       Time_taken(min)   distance  
0                   24   3.025149  
1                   33  20.183530  
2                   26   1.552758  
3                   21   7.790401  
4                   30   6.210138  
...                ...        ...  
45588               32   1.489846  
45589               36  11.007735  
45590               16   4.657195  
45591               26   6.232393  
45592               36  12.074396  

[45593 rows x 12 columns]

In [ ]:
dfi.export(dataframe,"df_distance.png",max_rows=10,table_conversion='crome',fontsize=10)

In [ ]:
figure = px.scatter(data_frame = dataframe, 
                    x="distance",
                    y="Time_taken(min)", 
                    size="Time_taken(min)", 
                    trendline="expanding" ,
                    title = "Relationship Between Distance and Time")
figure.show()

In [ ]:
figure = px.scatter(data_frame = dataframe, 
                    x="Delivery_person_Age",
                    y="Time_taken(min)", 
                    size="Time_taken(min)", 
                    color = "distance",
                    trendline="ols", 
                    title = "Relationship Between Time and Age")
figure.show()

In [ ]:
figure = px.scatter(data_frame = dataframe, 
                    x="Delivery_person_Ratings",
                    y="Time_taken(min)", 
                    size="Time_taken(min)", 
                    color = "distance",
                    trendline="ols", 
                    title = "Relationship Between Time and Ratings")
figure.show()

In [ ]:
fig = px.box(dataframe, 
             x="Type_of_vehicle",
             y="Time_taken(min)", 
             color="Type_of_order",
             labels={"Type_of_vehicle": "Vehicle","Time_taken(min)":"Time"})
fig.show()

In [ ]:
le = LabelEncoder()

dataframe['Type_of_vehicle'] = le.fit_transform(dataframe['Type_of_vehicle'])
vehicle_label = le.classes_
dataframe['Type_of_order'] = le.fit_transform(dataframe['Type_of_order'])
order_label = le.classes_
dataframe

ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0      4607     INDORES13DEL02                   37                      4.9   
1      B379     BANGRES18DEL02                   34                      4.5   
2      5D6D     BANGRES19DEL01                   23                      4.4   
3      7A6A    COIMBRES13DEL02                   38                      4.7   
4      70A2     CHENRES12DEL01                   32                      4.6   
...     ...                ...                  ...                      ...   
45588  7C09      JAPRES04DEL01                   30                      4.8   
45589  D641      AGRRES16DEL01                   21                      4.6   
45590  4F8D     CHENRES08DEL03                   30                      4.9   
45591  5EEE    COIMBRES11DEL01                   20                      4.7   
45592  5FB2   RANCHIRES09DEL02                   23                      4.9   

       Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0                22.745049             75.892471                   22.765049   
1                12.913041             77.683237                   13.043041   
2                12.914264             77.678400                   12.924264   
3                11.003669             76.976494                   11.053669   
4                12.972793             80.249982                   13.012793   
...                    ...                   ...                         ...   
45588            26.902328             75.794257                   26.912328   
45589             0.000000              0.000000                    0.070000   
45590            13.022394             80.242439                   13.052394   
45591            11.001753             76.986241                   11.041753   
45592            23.351058             85.325731                   23.431058   

       Delivery_location_longitude  Type_of_order  Type_of_vehicle  \
0                        75.912471              3                2   
1                        77.813237              3                3   
2                        77.688400              1                2   
3                        77.026494              0                2   
4                        80.289982              3                3   
...                            ...            ...              ...   
45588                    75.804257              2                2   
45589                     0.070000              0                2   
45590                    80.272439              1                3   
45591                    77.026241              3                2   
45592                    85.405731              3                3   

       Time_taken(min)   distance  
0                   24   3.025149  
1                   33  20.183530  
2                   26   1.552758  
3                   21   7.790401  
4                   30   6.210138  
...                ...        ...  
45588               32   1.489846  
45589               36  11.007735  
45590               16   4.657195  
45591               26   6.232393  
45592               36  12.074396  

[45593 rows x 12 columns]

In [ ]:
dfi.export(dataframe,"label_encode.png",max_rows=10,table_conversion='crome',fontsize=8)

In [ ]:
# x variable store features column with value.
# Also note that not store resturant and delivery location longetude and lattitude
# Becuse distance column create by this two column.
x = np.array(dataframe[["Delivery_person_Age", 
                   "Delivery_person_Ratings", 
                   "distance",
                   'Type_of_vehicle',
                   'Type_of_order']])

# y variable store target column 
y = np.array(dataframe[["Time_taken(min)"]])


# If above step complete now split them train and test set 
xtrain, xtest, ytrain, ytest = train_test_split(x, y, 
                                                test_size=0.10, 
                                                random_state=42)

xtrain


array([[33.        ,  4.6       ,  6.21785141,  2.        ,  0.        ],
       [24.        ,  4.5       , 10.58691052,  3.        ,  0.        ],
       [30.        ,  4.8       ,  9.43520154,  2.        ,  3.        ],
       ...,
       [39.        ,  4.9       ,  6.1220948 ,  2.        ,  2.        ],
       [25.        ,  4.9       ,  7.76093778,  3.        ,  2.        ],
       [31.        ,  4.6       ,  9.2208818 ,  2.        ,  0.        ]])

In [ ]:
model = Sequential()
model.add(LSTM(128,return_sequences=True,input_shape=(xtrain.shape[1],1)))
model.add(GRU(128,return_sequences=False))
model.add(Dense(64))
model.add(Dropout(0.2))
model.add(Dense(1))

model.summary()

Model: "sequential_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_11 (LSTM)              (None, 5, 128)            66560     
                                                                 
 gru_8 (GRU)                 (None, 128)               99072     
                                                                 
 dense_9 (Dense)             (None, 64)                8256      
                                                                 
 dropout_4 (Dropout)         (None, 64)                0         
                                                                 
 dense_10 (Dense)            (None, 1)                 65        
                                                                 
Total params: 173,953
Trainable params: 173,953
Non-trainable params: 0
_________________________________________________________________


In [ ]:
model.compile(optimizer=tf.keras.optimizers.Adam(),
               loss='mean_squared_error')
model.fit(xtrain,ytrain,batch_size=1,epochs=9)

Epoch 1/9
41033/41033 [==============================] - 272s 7ms/step - loss: 74.2674
Epoch 2/9
41033/41033 [==============================] - 251s 6ms/step - loss: 66.6880
Epoch 3/9
41033/41033 [==============================] - 249s 6ms/step - loss: 64.3554
Epoch 4/9
41033/41033 [==============================] - 232s 6ms/step - loss: 62.8772
Epoch 5/9
41033/41033 [==============================] - 239s 6ms/step - loss: 62.0591
Epoch 6/9
41033/41033 [==============================] - 247s 6ms/step - loss: 61.3976
Epoch 7/9
41033/41033 [==============================] - 248s 6ms/step - loss: 61.0095
Epoch 8/9
41033/41033 [==============================] - 254s 6ms/step - loss: 60.3753
Epoch 9/9
41033/41033 [==============================] - 265s 6ms/step - loss: 61.0530


In [ ]:
model.evaluate(xtest,ytest)

143/143 [==============================] - 2s 4ms/step - loss: 54.6020


54.60203552246094

In [ ]:
print("Real Time Food Delivery Time Prediction")
age = int(input("Age of Delivery Partner: "))
rating = float(input("Ratings of Previous Deliveries: "))
total_distance = float(input("Total Distance: "))
type_vehicle = int(input('''Type Of Vehicle Options \n(0) bicycle \n(1) electric scooter \n(2) motorcycle \n(3) scooter
             Choose One of these: ''')) 
type_order = int(input('''\nType Of Order Options \n(0) Buffet \n(1) Drink \n(2) Meal \n(3) Snack 
              Choose One Of these: ''')) 
features = np.array([[age, rating, total_distance,type_vehicle,type_order]])
print("\nPredicted Delivery Time in Minutes = ", round(float(model.predict(features))))

Real Time Food Delivery Time Prediction
Age of Delivery Partner: 20
Ratings of Previous Deliveries: 3.3
Total Distance: 2.3
Type Of Vehicle Options 
(0) bicycle 
(1) electric scooter 
(2) motorcycle 
(3) scooter
             Choose One of these: 0

Type Of Order Options 
(0) Buffet 
(1) Drink 
(2) Meal 
(3) Snack 
              Choose One Of these: 3
1/1 [==============================] - 1s 870ms/step

Predicted Delivery Time in Minutes =  33
